In [4]:
pip install opencv-python


In [5]:
# ✅ Imports
import os
import cv2
import numpy as np
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import ConvLSTM2D, BatchNormalization, Flatten, Dense, Dropout
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau


In [7]:
# ✅ Frame extraction function
def extract_frames(video_path, max_frames=30, size=(64, 64)):
    cap = cv2.VideoCapture(video_path)
    frames = []
    count = 0
    while cap.isOpened() and count < max_frames:
        ret, frame = cap.read()
        if not ret:
            break
        frame = cv2.resize(frame, size)
        frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
        frame = frame / 255.0
        frames.append(frame)
        count += 1
    cap.release()
    return np.array(frames) if len(frames) == max_frames else None


In [8]:
# ✅ Load dataset from violence/non-violence folders
def load_dataset_from_folder(violence_dir, nonviolence_dir, max_frames=30, size=(64, 64)):
    X, y = [], []
    for file in os.listdir(violence_dir):
        if file.endswith((".mp4", ".avi")):
            path = os.path.join(violence_dir, file)
            frames = extract_frames(path, max_frames=max_frames, size=size)
            if frames is not None:
                X.append(frames)
                y.append(1)
    for file in os.listdir(nonviolence_dir):
        if file.endswith((".mp4", ".avi")):
            path = os.path.join(nonviolence_dir, file)
            frames = extract_frames(path, max_frames=max_frames, size=size)
            if frames is not None:
                X.append(frames)
                y.append(0)
    return np.array(X)[..., np.newaxis], np.array(y)


In [ ]:
# ✅ 3. Load dataset
def load_dataset_from_folder(violence_dir, nonviolence_dir, max_frames=30, size=(64, 64)):
    X, y = [], []

    for file in os.listdir(violence_dir):
        if file.endswith((".mp4", ".avi")):
            path = os.path.join(violence_dir, file)
            frames = extract_frames(path, max_frames=max_frames, size=size)
            if frames is not None:
                X.append(frames)
                y.append(1)

    for file in os.listdir(nonviolence_dir):
        if file.endswith((".mp4", ".avi")):
            path = os.path.join(nonviolence_dir, file)
            frames = extract_frames(path, max_frames=max_frames, size=size)
            if frames is not None:
                X.append(frames)
                y.append(0)

    X = np.array(X)[..., np.newaxis]  # Add channel dimension
    y = np.array(y)
    return X, y


Dataset shape: (1000, 30, 64, 64, 1) (1000,)
Train: (800, 30, 64, 64, 1) Test: (200, 30, 64, 64, 1)


In [10]:
# ✅ 4. Load and split data
violence_path = "Real Life Violence Dataset/Violence"
nonviolence_path = "Real Life Violence Dataset/NonViolence"

X, y = load_dataset_from_folder(violence_path, nonviolence_path)
print("✅ Dataset loaded:", X.shape, y.shape)

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, stratify=y, random_state=42
)

print("🟢 Train:", X_train.shape)
print("🟡 Test:", X_test.shape)


✅ Dataset loaded: (1000, 30, 64, 64, 1) (1000,)
🟢 Train: (800, 30, 64, 64, 1)
🟡 Test: (200, 30, 64, 64, 1)


In [11]:
# ✅ 5. Define the ConvLSTM2D model
model = Sequential([
    ConvLSTM2D(filters=24, kernel_size=(3, 3), activation='relu',
               input_shape=(30, 64, 64, 1), return_sequences=False),
    BatchNormalization(),
    Flatten(),
    Dense(64, activation='relu'),
    Dropout(0.3),
    Dense(1, activation='sigmoid')
])

model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
model.summary()


c:\Users\ghala\anaconda3\Lib\site-packages\keras\src\layers\rnn\rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ conv_lstm2d (ConvLSTM2D)        │ (None, 62, 62, 24)     │        21,696 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 62, 62, 24)     │            96 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ flatten (Flatten)               │ (None, 92256)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 64)             │     5,904,448 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 64)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 1)              │            65 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 5,926,305 (22.61 MB)

 Trainable params: 5,926,257 (22.61 MB)

 Non-trainable params: 48 (192.00 B)

In [12]:
# ✅ 6. Train the model
early_stop = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)
reduce_lr = ReduceLROnPlateau(monitor='val_loss', patience=2, factor=0.5)

history = model.fit(
    X_train, y_train,
    validation_split=0.2,
    epochs=8,
    batch_size=8,
    callbacks=[early_stop, reduce_lr]
)


Epoch 1/8
80/80 ━━━━━━━━━━━━━━━━━━━━ 320s 4s/step - accuracy: 0.6036 - loss: 3.7787 - val_accuracy: 0.5188 - val_loss: 0.6926 - learning_rate: 0.0010
Epoch 2/8
80/80 ━━━━━━━━━━━━━━━━━━━━ 239s 3s/step - accuracy: 0.8172 - loss: 0.4290 - val_accuracy: 0.6187 - val_loss: 0.6642 - learning_rate: 0.0010
Epoch 3/8
80/80 ━━━━━━━━━━━━━━━━━━━━ 239s 3s/step - accuracy: 0.8753 - loss: 0.2452 - val_accuracy: 0.5938 - val_loss: 0.6352 - learning_rate: 0.0010
Epoch 4/8
80/80 ━━━━━━━━━━━━━━━━━━━━ 221s 3s/step - accuracy: 0.9532 - loss: 0.1445 - val_accuracy: 0.8125 - val_loss: 0.5249 - learning_rate: 0.0010
Epoch 5/8
80/80 ━━━━━━━━━━━━━━━━━━━━ 281s 3s/step - accuracy: 0.9711 - loss: 0.0895 - val_accuracy: 0.7375 - val_loss: 0.5090 - learning_rate: 0.0010
Epoch 6/8
80/80 ━━━━━━━━━━━━━━━━━━━━ 225s 3s/step - accuracy: 0.9822 - loss: 0.0538 - val_accuracy: 0.8000 - val_loss: 0.4571 - learning_rate: 0.0010
Epoch 7/8
80/80 ━━━━━━━━━━━━━━━━━━━━ 234s 3s/step - accuracy: 0.9922 - loss: 0.0366 - val_accuracy: 

In [13]:
# ✅ 7. Evaluate the model
test_loss, test_acc = model.evaluate(X_test, y_test)
print(f"📊 Test Accuracy: {test_acc:.2f}")


7/7 ━━━━━━━━━━━━━━━━━━━━ 82s 4s/step - accuracy: 0.7802 - loss: 0.3808
📊 Test Accuracy: 0.79


In [14]:
# ✅ 8. Save the model
model.save("models/fight_detection_model.h5")
print("💾 Model saved successfully.")


💾 Model saved successfully.


In [8]:
import os
import cv2
import numpy as np
import random
from tensorflow.keras.models import load_model
from base64 import b64encode
from IPython.display import HTML, display

# === Paths ===
model_path = "models/fight_detection_model.h5"
violence_dir = "Real Life Violence Dataset/Violence"
nonviolence_dir = "Real Life Violence Dataset/NonViolence"
frame_size = (64, 64)
max_frames = 30

# === Load model ===
model = load_model(model_path)

# === Frame extraction ===
def extract_frames(video_path, max_frames=30, size=(64, 64)):
    cap = cv2.VideoCapture(video_path)
    frames = []
    while cap.isOpened() and len(frames) < max_frames:
        ret, frame = cap.read()
        if not ret:
            break
        frame = cv2.resize(frame, size)
        frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
        frame = frame / 255.0
        frames.append(frame)
    cap.release()
    return np.array(frames)[np.newaxis, ..., np.newaxis] if len(frames) == max_frames else None

# === Display video inline ===
def show_video_inline(video_path):
    video = open(video_path, 'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(video).decode()
    return HTML(f"""
    <video width=400 controls>
        <source src="{data_url}" type="video/mp4">
    </video>
    """)

# === Predict and Display ===
def predict_and_display(video_path):
    frames = extract_frames(video_path)
    if frames is None:
        print(f"Not enough frames in: {video_path}")
        return

    pred = model.predict(frames)[0][0]
    label = "Violence" if pred >= 0.5 else "Non-Violence"
    confidence = pred if pred >= 0.5 else 1 - pred
    print(f"File: {os.path.basename(video_path)}")
    print(f"Predicted: {label} ({confidence * 100:.2f}%)")
    display(show_video_inline(video_path))

# === Run for one video from each class ===
violence_video = random.choice([f for f in os.listdir(violence_dir) if f.endswith(".mp4")])
nonviolence_video = random.choice([f for f in os.listdir(nonviolence_dir) if f.endswith(".mp4")])

predict_and_display(os.path.join(violence_dir, violence_video))
predict_and_display(os.path.join(nonviolence_dir, nonviolence_video))


1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step
File: V_417.mp4
Predicted: Violence (94.25%)


1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 847ms/step
File: NV_339.mp4
Predicted: Non-Violence (96.30%)


In [14]:
import os
import cv2
import numpy as np
import random
from tensorflow.keras.models import load_model
from base64 import b64encode
from IPython.display import HTML, display

# === Settings ===
model_path = "models/fight_detection_model.h5"
violence_dir = "Real Life Violence Dataset/Violence"
nonviolence_dir = "Real Life Violence Dataset/NonViolence"
frame_size = (64, 64)
max_frames = 30

# === Load model ===
model = load_model(model_path)

# === Extract frames from video ===
def extract_frames(video_path, max_frames=30, size=(64, 64)):
    cap = cv2.VideoCapture(video_path)
    frames = []
    while cap.isOpened() and len(frames) < max_frames:
        ret, frame = cap.read()
        if not ret:
            break
        frame = cv2.resize(frame, size)
        frame = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
        frame = frame / 255.0
        frames.append(frame)
    cap.release()
    return np.array(frames)[np.newaxis, ..., np.newaxis] if len(frames) == max_frames else None

# === Display video inline ===
def show_video_inline(video_path):
    video = open(video_path, 'rb').read()
    data_url = "data:video/mp4;base64," + b64encode(video).decode()
    return HTML(f"""
    <video width=400 controls>
        <source src="{data_url}" type="video/mp4">
    </video>
    """)

# === Predict and Display with Actual Label ===
def predict_and_display(video_path, actual_label):
    frames = extract_frames(video_path)
    if frames is None:
        print(f"❌ Not enough frames in: {video_path}")
        return

    pred = model.predict(frames)[0][0]
    predicted_label = "Violence" if pred >= 0.5 else "Non-Violence"
    confidence = pred if pred >= 0.5 else 1 - pred

    print(f"\n🎞️ File: {os.path.basename(video_path)}")
    print(f" Actual label: {actual_label}")
    print(f" Predicted: {predicted_label} ({confidence * 100:.2f}%)")

    display(show_video_inline(video_path))

# === Select one random video from each class ===
violence_video = random.choice([f for f in os.listdir(violence_dir) if f.endswith(".mp4")])
nonviolence_video = random.choice([f for f in os.listdir(nonviolence_dir) if f.endswith(".mp4")])

predict_and_display(os.path.join(violence_dir, violence_video), actual_label="Violence")
predict_and_display(os.path.join(nonviolence_dir, nonviolence_video), actual_label="Non-Violence")


1/1 ━━━━━━━━━━━━━━━━━━━━ 2s 2s/step

🎞️ File: V_324.mp4
 Actual label: Violence
 Predicted: Violence (97.47%)


1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step

🎞️ File: NV_220.mp4
 Actual label: Non-Violence
 Predicted: Non-Violence (97.51%)
